# 🗞️ Clustering Semántico de Noticias usando BERT y HDBSCAN

Este notebook implementa un sistema completo de clustering semántico de noticias utilizando:
- **BERT** (all-MiniLM-L6-v2) para embeddings semánticos
- **UMAP** para reducción de dimensionalidad a 5D (óptimo para clustering)
- **HDBSCAN** para clustering automático sin especificar número de clusters
- **Visualización interactiva** con Plotly

**Autor**: Senior Data Scientist
**Compatible con**: Google Colab y entornos locales


## 📦 Instalación de dependencias (ejecutar solo en Google Colab)

In [30]:
# Descomentar la siguiente línea si ejecutas en Google Colab
!pip install -q sentence-transformers umap-learn hdbscan kagglehub plotly seaborn scikit-learn tqdm



[notice] A new release of pip is available: 26.0 -> 26.0.1
[notice] To update, run: pip install --upgrade pip


## 📚 Importación de librerías

In [31]:
import warnings
import re
import os
from collections import Counter
from typing import Tuple, List, Optional, Dict

import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
import umap
import hdbscan
from sklearn.metrics import pairwise_distances
import plotly.express as px
import plotly.graph_objects as go
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.patches import Patch
import kagglehub
from tqdm import tqdm

# Configuración
warnings.filterwarnings('ignore')
pd.set_option('display.max_colwidth', 100)

print("✅ Todas las librerías importadas correctamente")


✅ Todas las librerías importadas correctamente


## 🔧 FUNCIÓN 1: Carga de Datos desde Kaggle

In [32]:
def load_news_dataset(sample_size: Optional[int] = None) -> pd.DataFrame:
    """
    Carga el News Category Dataset desde Kaggle y prepara los datos.

    Pasos:
    1. Descarga el dataset usando kagglehub
    2. Busca el archivo JSON en el directorio
    3. Concatena 'headline' + 'short_description' en columna 'text'
    4. Limpia filas vacías
    5. Opcionalmente toma una muestra aleatoria

    Args:
        sample_size: Número de noticias a cargar (None para todo el dataset)

    Returns:
        DataFrame con columnas: headline, short_description, text, category, etc.

    Raises:
        FileNotFoundError: Si no se encuentra el archivo JSON
        ValueError: Si faltan columnas requeridas
    """
    try:
        print("📥 Descargando dataset desde Kaggle...")
        path = kagglehub.dataset_download("rmisra/news-category-dataset")
        print(f"✅ Dataset descargado en: {path}")

        # Buscar archivo JSON
        json_files = [f for f in os.listdir(path) if f.endswith('.json')]
        if not json_files:
            raise FileNotFoundError("No se encontró archivo JSON en el dataset")

        json_path = os.path.join(path, json_files[0])
        print(f"📄 Cargando archivo: {json_path}")

        # Cargar dataset (formato JSON lines)
        df = pd.read_json(json_path, lines=True)

        # Verificar columnas requeridas
        required_cols = ['headline', 'short_description']
        missing_cols = [col for col in required_cols if col not in df.columns]
        if missing_cols:
            raise ValueError(f"Columnas faltantes: {missing_cols}")

        # Concatenar headline + short_description en 'text'
        print("🔗 Concatenando 'headline' y 'short_description' en columna 'text'...")
        df['text'] = df['headline'].fillna('') + ' ' + df['short_description'].fillna('')
        df['text'] = df['text'].str.strip()

        # Eliminar filas vacías
        df = df[df['text'].str.len() > 0].reset_index(drop=True)

        # Aplicar muestra si se especifica
        if sample_size and sample_size < len(df):
            df = df.sample(n=sample_size, random_state=42).reset_index(drop=True)
            print(f"📊 Muestra seleccionada: {sample_size} noticias")

        print(f"✅ Dataset cargado: {len(df)} noticias")
        print(f"   Columnas: {df.columns.tolist()}")

        return df

    except Exception as e:
        print(f"❌ Error al cargar dataset: {str(e)}")
        raise


## 🧹 FUNCIÓN 2: Preprocesamiento de Texto

In [33]:
def preprocess_text(text: str) -> str:
    """
    Realiza limpieza básica del texto manteniendo estructura semántica para BERT.

    Operaciones:
    - Convierte a minúsculas
    - Elimina URLs
    - Remueve caracteres especiales (mantiene letras, números, puntuación básica)
    - Normaliza espacios múltiples

    Args:
        text: Texto a preprocesar

    Returns:
        Texto limpio en minúsculas
    """
    if not isinstance(text, str):
        return ""

    # Convertir a minúsculas
    text = text.lower()

    # Remover URLs
    text = re.sub(r'http\S+|www\S+', '', text)

    # Remover caracteres especiales (mantener estructura para BERT)
    text = re.sub(r'[^a-záéíóúüñ0-9\s.,!?\'\-]', ' ', text)

    # Normalizar espacios
    text = re.sub(r'\s+', ' ', text)

    return text.strip()


def preprocess_dataframe(df: pd.DataFrame, text_column: str = 'text') -> pd.DataFrame:
    """
    Aplica preprocesamiento a todo el DataFrame.

    Args:
        df: DataFrame con los datos
        text_column: Nombre de la columna a preprocesar

    Returns:
        DataFrame con columna 'text_clean' añadida
    """
    print("🧹 Preprocesando textos...")

    # Aplicar preprocesamiento con progreso
    tqdm.pandas(desc="Limpieza de texto")
    df['text_clean'] = df[text_column].progress_apply(preprocess_text)

    # Eliminar textos muy cortos
    initial_count = len(df)
    df = df[df['text_clean'].str.len() > 10].reset_index(drop=True)
    removed = initial_count - len(df)

    print(f"✅ Preprocesamiento completado")
    print(f"   - Textos procesados: {len(df)}")
    print(f"   - Textos eliminados (muy cortos): {removed}")

    return df


## 🤖 FUNCIÓN 3: Generación de Embeddings con BERT

In [34]:
def generate_embeddings(
    texts: List[str],
    model_name: str = 'all-MiniLM-L6-v2',
    batch_size: int = 64,
    show_progress: bool = True
) -> np.ndarray:
    """
    Genera embeddings semánticos usando Sentence-BERT.

    Args:
        texts: Lista de textos a vectorizar
        model_name: Modelo de sentence-transformers
        batch_size: Tamaño de batch para procesamiento
        show_progress: Mostrar barra de progreso

    Returns:
        Array numpy con embeddings (n_samples, 384)

    Raises:
        RuntimeError: Si hay error al generar embeddings
    """
    try:
        print(f"🤖 Cargando modelo BERT: '{model_name}'...")
        model = SentenceTransformer(model_name)
        print(f"✅ Modelo cargado")
        print(f"   - Dimensión de embeddings: {model.get_sentence_embedding_dimension()}")

        print(f"\n🔄 Generando embeddings para {len(texts)} textos...")
        embeddings = model.encode(
            texts,
            batch_size=batch_size,
            show_progress_bar=show_progress,
            convert_to_numpy=True
        )

        print(f"✅ Embeddings generados: shape = {embeddings.shape}")
        return embeddings

    except Exception as e:
        print(f"❌ Error al generar embeddings: {str(e)}")
        raise RuntimeError(f"Error en generación de embeddings: {str(e)}")


## 📉 FUNCIÓN 4: Reducción de Dimensionalidad con UMAP

In [35]:
def reduce_dimensions(
    embeddings: np.ndarray,
    n_components: int = 5,
    n_neighbors: int = 15,
    min_dist: float = 0.0,
    metric: str = 'cosine',
    random_state: int = 42
) -> np.ndarray:
    """
    Reduce dimensionalidad de embeddings usando UMAP.

    IMPORTANTE: Se recomienda 5 dimensiones para clustering con HDBSCAN
    (balance entre preservar información y evitar curse of dimensionality)

    Args:
        embeddings: Array de embeddings de alta dimensión
        n_components: Dimensiones objetivo (5 para clustering, 2 para visualización)
        n_neighbors: Número de vecinos (estructura local vs global)
        min_dist: Distancia mínima entre puntos
        metric: Métrica de distancia (cosine para similitud semántica)
        random_state: Semilla para reproducibilidad

    Returns:
        Array con embeddings reducidos
    """
    try:
        print(f"📉 Reduciendo dimensionalidad con UMAP...")
        print(f"   - De {embeddings.shape[1]}D → {n_components}D")

        reducer = umap.UMAP(
            n_components=n_components,
            n_neighbors=n_neighbors,
            min_dist=min_dist,
            metric=metric,
            random_state=random_state,
            verbose=True
        )

        embeddings_reduced = reducer.fit_transform(embeddings)

        print(f"✅ Reducción completada: {embeddings_reduced.shape}")
        return embeddings_reduced

    except Exception as e:
        print(f"❌ Error en UMAP: {str(e)}")
        raise


## 🔍 FUNCIÓN 5: Clustering con HDBSCAN

In [36]:
def perform_clustering(
    embeddings: np.ndarray,
    min_cluster_size: int = 100,
    min_samples: int = 15,
    metric: str = 'euclidean'
) -> Tuple[np.ndarray, hdbscan.HDBSCAN]:
    """
    Realiza clustering usando HDBSCAN (detección automática de clusters).

    HDBSCAN ventajas:
    - No requiere especificar número de clusters
    - Robusto al ruido (etiqueta outliers como -1)
    - Clusters de tamaños variables

    Args:
        embeddings: Embeddings reducidos (preferiblemente 5D)
        min_cluster_size: Mínimo de noticias por cluster (↑ = menos clusters)
        min_samples: Mínimo de muestras para core points (↑ = más estricto)
        metric: Métrica de distancia

    Returns:
        Tuple (labels, modelo_hdbscan)
        - labels: Array con cluster_id por noticia (-1 = ruido)
        - modelo: Objeto HDBSCAN entrenado
    """
    try:
        print(f"🔍 Ejecutando HDBSCAN...")
        print(f"   - min_cluster_size: {min_cluster_size}")
        print(f"   - min_samples: {min_samples}")

        clusterer = hdbscan.HDBSCAN(
            min_cluster_size=min_cluster_size,
            min_samples=min_samples,
            metric=metric,
            cluster_selection_method='eom',  # Excess of Mass
            prediction_data=True
        )

        labels = clusterer.fit_predict(embeddings)

        # Estadísticas
        n_clusters = len(set(labels)) - (1 if -1 in labels else 0)
        n_noise = (labels == -1).sum()
        noise_ratio = n_noise / len(labels) * 100

        print(f"\n✅ Clustering completado:")
        print(f"   - Clusters encontrados: {n_clusters}")
        print(f"   - Puntos de ruido: {n_noise} ({noise_ratio:.1f}%)")

        # Distribución
        print(f"\n📊 Distribución de clusters:")
        cluster_counts = pd.Series(labels).value_counts().sort_index()
        for cluster_id, count in cluster_counts.items():
            label = "Ruido" if cluster_id == -1 else f"Cluster {cluster_id}"
            print(f"   - {label}: {count} noticias")

        return labels, clusterer

    except Exception as e:
        print(f"❌ Error en clustering: {str(e)}")
        raise


## 📊 FUNCIÓN 6: Visualización Interactiva con Plotly

In [37]:
def visualize_clusters_plotly(
    embeddings_2d: np.ndarray,
    labels: np.ndarray,
    df: pd.DataFrame,
    cluster_names: Optional[Dict[int, str]] = None,
    title: str = "Clustering Semántico de Noticias"
) -> go.Figure:
    """
    Genera visualización interactiva de clusters con Plotly.

    Características:
    - Hover muestra headline completo
    - Zoom y pan interactivos
    - Colores por cluster con nombres descriptivos

    Args:
        embeddings_2d: Embeddings reducidos a 2D (para eje X e Y)
        labels: Labels de cluster por noticia
        df: DataFrame con datos originales
        cluster_names: Diccionario opcional con nombres descriptivos {cluster_id: nombre}
        title: Título del gráfico

    Returns:
        Figura de Plotly (usar .show() para mostrar)
    """
    print("📊 Generando visualización interactiva...")

    # Asignar nombres descriptivos si están disponibles
    if cluster_names:
        cluster_labels = [cluster_names.get(label, f"Cluster {label}") for label in labels]
    else:
        cluster_labels = [f"Cluster {label}" if label != -1 else "Ruido" for label in labels]

    # Preparar datos para plotly
    viz_df = pd.DataFrame({
        'x': embeddings_2d[:, 0],
        'y': embeddings_2d[:, 1],
        'cluster': cluster_labels,
        'cluster_id': labels,
        'headline': df['headline'].values,
        'text_preview': df['text_clean'].str[:100] + '...'
    })

    # Crear figura
    fig = px.scatter(
        viz_df,
        x='x',
        y='y',
        color='cluster',
        hover_data=['headline', 'text_preview', 'cluster_id'],
        title=title,
        labels={'x': 'UMAP 1', 'y': 'UMAP 2', 'cluster': 'Cluster'},
        opacity=0.7
    )

    fig.update_layout(
        width=1000,
        height=700,
        template='plotly_white',
        legend_title_text='Cluster'
    )

    fig.update_traces(marker=dict(size=5))

    print("✅ Visualización generada")
    return fig


## 🏷️ FUNCIÓN 7: Interpretación - Top Términos por Cluster

In [38]:
def get_top_terms_per_cluster(
    df: pd.DataFrame,
    text_column: str = 'text_clean',
    cluster_column: str = 'cluster',
    n_terms: int = 5,
    min_word_length: int = 3
) -> Dict[int, List[Tuple[str, int]]]:
    """
    Obtiene los términos más frecuentes para cada cluster.

    Args:
        df: DataFrame con datos y clusters
        text_column: Columna con texto preprocesado
        cluster_column: Columna con labels de cluster
        n_terms: Número de términos a retornar
        min_word_length: Longitud mínima de palabras

    Returns:
        Dict con {cluster_id: [(palabra, frecuencia), ...]}
    """
    # Stopwords básicas en inglés
    stopwords = {
        'the', 'a', 'an', 'and', 'or', 'but', 'in', 'on', 'at', 'to', 'for',
        'of', 'with', 'by', 'from', 'as', 'is', 'was', 'are', 'were', 'been',
        'be', 'have', 'has', 'had', 'do', 'does', 'did', 'will', 'would',
        'could', 'should', 'may', 'might', 'must', 'can', 'it', 'its', 'this',
        'that', 'these', 'those', 'what', 'when', 'where', 'why', 'how', 'all',
        'just', 'about', 'your', 'new', 'one', 'two', 'first', 'after', 'over'
    }

    cluster_terms = {}
    unique_clusters = sorted([c for c in df[cluster_column].unique() if c != -1])

    for cluster_id in unique_clusters:
        # Obtener textos del cluster
        cluster_texts = df[df[cluster_column] == cluster_id][text_column].tolist()

        # Tokenizar y contar
        all_words = []
        for text in cluster_texts:
            words = text.split()
            words = [w for w in words if len(w) >= min_word_length and w not in stopwords]
            all_words.extend(words)

        # Top términos
        word_counts = Counter(all_words)
        top_terms = word_counts.most_common(n_terms)
        cluster_terms[cluster_id] = top_terms

    return cluster_terms


def generate_cluster_names(cluster_terms: Dict[int, List[Tuple[str, int]]]) -> Dict[int, str]:
    """
    Genera nombres descriptivos para cada cluster basándose en sus términos más frecuentes.

    Args:
        cluster_terms: Diccionario con top términos por cluster

    Returns:
        Dict con {cluster_id: "Nombre Descriptivo"}
    """
    cluster_names = {}

    for cluster_id, terms in cluster_terms.items():
        if terms:
            # Usar los 2-3 términos principales para crear el nombre
            top_words = [term[0].capitalize() for term in terms[:3]]
            cluster_name = " & ".join(top_words[:2])
            if len(top_words) > 2:
                cluster_name += f" ({top_words[2]})"
            cluster_names[cluster_id] = cluster_name
        else:
            cluster_names[cluster_id] = f"Cluster {cluster_id}"

    # Añadir nombre para ruido
    cluster_names[-1] = "Ruido (No clasificado)"

    return cluster_names


def apply_cluster_names(df: pd.DataFrame, cluster_names: Dict[int, str]) -> pd.DataFrame:
    """
    Aplica nombres descriptivos a los clusters en el DataFrame.

    Args:
        df: DataFrame con columna 'cluster'
        cluster_names: Diccionario con nombres de clusters

    Returns:
        DataFrame con columna 'cluster_name' añadida
    """
    df['cluster_name'] = df['cluster'].map(cluster_names)
    return df


## 📰 FUNCIÓN 8: Interpretación - Titulares Representativos

In [39]:
def get_representative_headlines(
    df: pd.DataFrame,
    embeddings: np.ndarray,
    cluster_column: str = 'cluster',
    n_headlines: int = 3
) -> Dict[int, List[str]]:
    """
    Obtiene los titulares más representativos de cada cluster
    (los más cercanos al centroide del cluster).

    Args:
        df: DataFrame con datos
        embeddings: Embeddings de las noticias (5D recomendado)
        cluster_column: Columna con labels de cluster
        n_headlines: Número de titulares a retornar

    Returns:
        Dict con {cluster_id: [headline1, headline2, ...]}
    """
    representative_headlines = {}
    unique_clusters = sorted([c for c in df[cluster_column].unique() if c != -1])

    for cluster_id in unique_clusters:
        # Máscaras e índices
        cluster_mask = df[cluster_column] == cluster_id
        cluster_indices = df[cluster_mask].index.tolist()
        cluster_embeddings = embeddings[cluster_mask]

        # Calcular centroide
        centroid = cluster_embeddings.mean(axis=0).reshape(1, -1)

        # Distancias al centroide
        distances = pairwise_distances(cluster_embeddings, centroid, metric='cosine').flatten()

        # Índices más cercanos
        closest_indices = np.argsort(distances)[:n_headlines]

        # Obtener titulares
        headlines = [df.iloc[cluster_indices[i]]['headline'] for i in closest_indices]
        representative_headlines[cluster_id] = headlines

    return representative_headlines


## 📋 FUNCIÓN 9: Generar Resumen de Clusters

In [40]:
def print_cluster_interpretation(
    cluster_terms: Dict[int, List[Tuple[str, int]]],
    representative_headlines: Dict[int, List[str]],
    df: pd.DataFrame
):
    """
    Imprime interpretación completa de cada cluster.

    Args:
        cluster_terms: Diccionario con top términos
        representative_headlines: Diccionario con titulares representativos
        df: DataFrame con datos y clusters
    """
    print("\n" + "="*70)
    print("📝 INTERPRETACIÓN DE CLUSTERS")
    print("="*70)

    for cluster_id in sorted(cluster_terms.keys()):
        cluster_size = len(df[df['cluster'] == cluster_id])

        print(f"\n🏷️  CLUSTER {cluster_id} ({cluster_size} noticias)")

        # Top términos
        terms_str = ', '.join([f"{term}({count})" for term, count in cluster_terms[cluster_id]])
        print(f"   📊 Top 5 términos: {terms_str}")

        # Titulares representativos
        print(f"   📰 Titulares representativos:")
        for i, headline in enumerate(representative_headlines[cluster_id], 1):
            print(f"      {i}. {headline}")


---
## 🚀 EJECUCIÓN DEL PIPELINE COMPLETO
---


### PASO 1: Carga de datos

In [41]:
# Ajusta sample_size según tu hardware:
# - 1000 para prueba rápida
# - 10000 para resultados buenos (recomendado)
# - None para dataset completo (~200K noticias, muy lento)

df = load_news_dataset(sample_size=10000)

# Mostrar ejemplos
print("\n📰 Ejemplos de noticias:")
print(df[['headline', 'text']].head(3))


📥 Descargando dataset desde Kaggle...
✅ Dataset descargado en: /Users/samuelsanchezheredia/.cache/kagglehub/datasets/rmisra/news-category-dataset/versions/3
📄 Cargando archivo: /Users/samuelsanchezheredia/.cache/kagglehub/datasets/rmisra/news-category-dataset/versions/3/News_Category_Dataset_v3.json
🔗 Concatenando 'headline' y 'short_description' en columna 'text'...
📊 Muestra seleccionada: 10000 noticias
✅ Dataset cargado: 10000 noticias
   Columnas: ['link', 'headline', 'category', 'short_description', 'authors', 'date', 'text']

📰 Ejemplos de noticias:
                                                                                    headline  \
0                Rick Snyder Says He's Releasing All His Emails About The Flint Water Crisis   
1  Mark Sanchez Pick Six: Bryan Scott Returns Interception For Touchdown In Jets-Bills (GIF)   
2                                                     Selena Gomez's AMAs Dress Is Very Sexy   

                                                     

### PASO 2: Preprocesamiento

In [42]:
df = preprocess_dataframe(df)

# Comparación antes/después
print("\n📝 Ejemplo de preprocesamiento:")
print(f"Original: {df['text'].iloc[0][:100]}...")
print(f"Limpio:   {df['text_clean'].iloc[0][:100]}...")


🧹 Preprocesando textos...


Limpieza de texto: 100%|██████████| 10000/10000 [00:00<00:00, 160480.57it/s]

✅ Preprocesamiento completado
   - Textos procesados: 9999
   - Textos eliminados (muy cortos): 1

📝 Ejemplo de preprocesamiento:
Original: Rick Snyder Says He's Releasing All His Emails About The Flint Water Crisis It's not clear when the ...
Limpio:   rick snyder says he's releasing all his emails about the flint water crisis it's not clear when the ...


### PASO 3: Generación de embeddings con BERT

In [43]:
embeddings = generate_embeddings(df['text_clean'].tolist())

print(f"\n📊 Estadísticas de embeddings:")
print(f"   - Shape: {embeddings.shape}")
print(f"   - Min: {embeddings.min():.4f}, Max: {embeddings.max():.4f}")


🤖 Cargando modelo BERT: 'all-MiniLM-L6-v2'...


Loading weights:   0%|          | 0/103 [00:00<?, ?it/s]

BertModel LOAD REPORT from: sentence-transformers/all-MiniLM-L6-v2
Key                     | Status     |  | 
------------------------+------------+--+-
embeddings.position_ids | UNEXPECTED |  | 

Notes:
- UNEXPECTED	:can be ignored when loading from different task/architecture; not ok if you expect identical arch.


✅ Modelo cargado
   - Dimensión de embeddings: 384

🔄 Generando embeddings para 9999 textos...


Batches:   0%|          | 0/157 [00:00<?, ?it/s]

✅ Embeddings generados: shape = (9999, 384)

📊 Estadísticas de embeddings:
   - Shape: (9999, 384)
   - Min: -0.2606, Max: 0.2642


### PASO 4: Reducción UMAP a 5D (para clustering)

In [44]:
# 5D es óptimo para HDBSCAN: preserva información sin curse of dimensionality
embeddings_5d = reduce_dimensions(embeddings, n_components=5)


📉 Reduciendo dimensionalidad con UMAP...
   - De 384D → 5D
UMAP(angular_rp_forest=True, metric='cosine', min_dist=0.0, n_components=5, n_jobs=1, random_state=42, verbose=True)
Tue Feb 17 12:21:54 2026 Construct fuzzy simplicial set
Tue Feb 17 12:21:54 2026 Finding Nearest Neighbors
Tue Feb 17 12:21:54 2026 Building RP forest with 10 trees
Tue Feb 17 12:21:55 2026 NN descent for 13 iterations
	 1  /  13
	 2  /  13
	 3  /  13
	 4  /  13
	 5  /  13
	 6  /  13
	Stopping threshold met -- exiting after 6 iterations
Tue Feb 17 12:21:55 2026 Finished Nearest Neighbor Search
Tue Feb 17 12:21:55 2026 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

	completed  0  /  500 epochs
	completed  50  /  500 epochs
	completed  100  /  500 epochs
	completed  150  /  500 epochs
	completed  200  /  500 epochs
	completed  250  /  500 epochs
	completed  300  /  500 epochs
	completed  350  /  500 epochs
	completed  400  /  500 epochs
	completed  450  /  500 epochs
Tue Feb 17 12:22:02 2026 Finished embedding
✅ Reducción completada: (9999, 5)


### PASO 5: Reducción UMAP a 2D (para visualización)

In [45]:
print("\n" + "="*50)
print("Generando versión 2D para visualización...")
embeddings_2d = reduce_dimensions(
    embeddings,
    n_components=2,
    n_neighbors=15,
    min_dist=0.1
)



Generando versión 2D para visualización...
📉 Reduciendo dimensionalidad con UMAP...
   - De 384D → 2D
UMAP(angular_rp_forest=True, metric='cosine', n_jobs=1, random_state=42, verbose=True)
Tue Feb 17 12:22:02 2026 Construct fuzzy simplicial set
Tue Feb 17 12:22:02 2026 Finding Nearest Neighbors
Tue Feb 17 12:22:02 2026 Building RP forest with 10 trees
Tue Feb 17 12:22:02 2026 NN descent for 13 iterations
	 1  /  13
	 2  /  13
	 3  /  13
	 4  /  13
	 5  /  13
	 6  /  13
	Stopping threshold met -- exiting after 6 iterations
Tue Feb 17 12:22:03 2026 Finished Nearest Neighbor Search
Tue Feb 17 12:22:03 2026 Construct embedding


Epochs completed:   0%|            0/500 [00:00]

	completed  0  /  500 epochs
	completed  50  /  500 epochs
	completed  100  /  500 epochs
	completed  150  /  500 epochs
	completed  200  /  500 epochs
	completed  250  /  500 epochs
	completed  300  /  500 epochs
	completed  350  /  500 epochs
	completed  400  /  500 epochs
	completed  450  /  500 epochs
Tue Feb 17 12:22:09 2026 Finished embedding
✅ Reducción completada: (9999, 2)


### PASO 6: Clustering con HDBSCAN

In [46]:
# Ajusta parámetros según necesidad:
# - min_cluster_size: ↑ = menos clusters más grandes, ↓ = más clusters pequeños
# - min_samples: ↑ = más estricto (menos ruido), ↓ = más flexible

labels, clusterer = perform_clustering(
    embeddings_5d,
    min_cluster_size=100,
    min_samples=15
)

# Añadir labels al DataFrame
df['cluster'] = labels


🔍 Ejecutando HDBSCAN...
   - min_cluster_size: 100
   - min_samples: 15

✅ Clustering completado:
   - Clusters encontrados: 18
   - Puntos de ruido: 3590 (35.9%)

📊 Distribución de clusters:
   - Ruido: 3590 noticias
   - Cluster 0: 259 noticias
   - Cluster 1: 205 noticias
   - Cluster 2: 238 noticias
   - Cluster 3: 586 noticias
   - Cluster 4: 426 noticias
   - Cluster 5: 369 noticias
   - Cluster 6: 119 noticias
   - Cluster 7: 203 noticias
   - Cluster 8: 668 noticias
   - Cluster 9: 635 noticias
   - Cluster 10: 184 noticias
   - Cluster 11: 553 noticias
   - Cluster 12: 703 noticias
   - Cluster 13: 192 noticias
   - Cluster 14: 114 noticias
   - Cluster 15: 152 noticias
   - Cluster 16: 686 noticias
   - Cluster 17: 117 noticias


### PASO 7: Visualización interactiva (preliminar)

In [47]:
# Visualización inicial sin nombres descriptivos
fig = visualize_clusters_plotly(embeddings_2d, labels, df)
fig.show()


📊 Generando visualización interactiva...
✅ Visualización generada


### PASO 8: Generación de nombres descriptivos para clusters

In [48]:
# Obtener términos frecuentes por cluster
cluster_terms = get_top_terms_per_cluster(df, n_terms=5)

# Generar nombres descriptivos basados en términos
cluster_names = generate_cluster_names(cluster_terms)

# Aplicar nombres al DataFrame
df = apply_cluster_names(df, cluster_names)

print("\n" + "="*70)
print("🏷️ NOMBRES DESCRIPTIVOS DE CLUSTERS")
print("="*70)

for cluster_id, name in sorted(cluster_names.items()):
    if cluster_id != -1:
        cluster_size = len(df[df['cluster'] == cluster_id])
        terms_str = ', '.join([f"{term}({count})" for term, count in cluster_terms[cluster_id]])
        print(f"\n🏷️  {name} (ID: {cluster_id}, {cluster_size} noticias)")
        print(f"   📊 Términos: {terms_str}")



🏷️ NOMBRES DESCRIPTIVOS DE CLUSTERS

🏷️  You & His (Game) (ID: 0, 259 noticias)
   📊 Términos: you(36), his(33), game(32), super(30), olympic(30)

🏷️  Dog & Animal (His) (ID: 1, 205 noticias)
   📊 Términos: dog(45), animal(33), his(28), cat(23), dogs(23)

🏷️  Climate & Change (Water) (ID: 2, 238 noticias)
   📊 Términos: climate(89), change(48), water(23), not(21), people(20)

🏷️  Police & Not (Gun) (ID: 3, 586 noticias)
   📊 Términos: police(79), not(72), gun(69), who(49), more(47)

🏷️  You & Their (Kids) (ID: 4, 426 noticias)
   📊 Términos: you(157), their(78), kids(76), her(74), our(72)

🏷️  Not & U.s. (Isis) (ID: 5, 369 noticias)
   📊 Términos: not(47), u.s.(45), isis(42), trump(36), president(30)

🏷️  Women & You (Her) (ID: 6, 119 noticias)
   📊 Términos: women(84), you(22), her(21), business(19), women's(16)

🏷️  Gay & Marriage (Transgender) (ID: 7, 203 noticias)
   📊 Términos: gay(74), marriage(38), transgender(32), lgbt(32), lgbtq(25)

🏷️  You & Photos (Travel) (ID: 8, 668 noti

### PASO 8b: Visualización con nombres descriptivos (después de generar nombres)

In [49]:
# Este bloque se puede ejecutar después del PASO 8 para ver la visualización con nombres
fig_named = visualize_clusters_plotly(embeddings_2d, labels, df, cluster_names)
fig_named.show()


📊 Generando visualización interactiva...
✅ Visualización generada


### PASO 9: Interpretación - Titulares representativos

In [50]:
representative = get_representative_headlines(df, embeddings_5d, n_headlines=3)

print("\n" + "="*70)
print("📰 TITULARES MÁS REPRESENTATIVOS POR CLUSTER")
print("="*70)

for cluster_id, headlines in representative.items():
    cluster_size = len(df[df['cluster'] == cluster_id])
    cluster_name = cluster_names.get(cluster_id, f"Cluster {cluster_id}")
    print(f"\n🏷️  {cluster_name} ({cluster_size} noticias):")
    for i, headline in enumerate(headlines, 1):
        print(f"   {i}. {headline}")



📰 TITULARES MÁS REPRESENTATIVOS POR CLUSTER

🏷️  You & His (Game) (259 noticias):
   1. WATCH: Rivals Brawl, Players Ejected After 'Cheap Shot' On Quarterback
   2. Olbermann: Clippers Should Refuse To Play
   3. Maybe Coin Tosses Aren't Entirely Random After All

🏷️  Dog & Animal (His) (205 noticias):
   1. PETA To Make A Killing Off Dentist-Slaying Lion Costume?
   2. Scientists Record Deer Gnawing On Human Remains For The First Time
   3. Furor Erupts After Australian Officials Kill Rescue Dogs Over COVID-19 Fears

🏷️  Climate & Change (Water) (238 noticias):
   1. Solving California's Water Problems
   2. Life-Giving Deltas Starved by Dams
   3. The Deadly Cost Of North Dakota's Gas Boom

🏷️  Police & Not (Gun) (586 noticias):
   1. Buffer Zones, Clinic Escorting, and the Myth of the Quiet Sidewalk Counselors
   2. Human Trafficking Survivor: I Was Raped 43,200 Times
   3. Neighbor Sent Letter Asking To 'Taste' Family's 'Delicious' Kids, Cops Say

🏷️  You & Their (Kids) (426 notic

### PASO 10: Resumen consolidado

In [51]:
print_cluster_interpretation(cluster_terms, representative, df)



📝 INTERPRETACIÓN DE CLUSTERS

🏷️  CLUSTER 0 (259 noticias)
   📊 Top 5 términos: you(36), his(33), game(32), super(30), olympic(30)
   📰 Titulares representativos:
      1. WATCH: Rivals Brawl, Players Ejected After 'Cheap Shot' On Quarterback
      2. Olbermann: Clippers Should Refuse To Play
      3. Maybe Coin Tosses Aren't Entirely Random After All

🏷️  CLUSTER 1 (205 noticias)
   📊 Top 5 términos: dog(45), animal(33), his(28), cat(23), dogs(23)
   📰 Titulares representativos:
      1. PETA To Make A Killing Off Dentist-Slaying Lion Costume?
      2. Scientists Record Deer Gnawing On Human Remains For The First Time
      3. Furor Erupts After Australian Officials Kill Rescue Dogs Over COVID-19 Fears

🏷️  CLUSTER 2 (238 noticias)
   📊 Top 5 términos: climate(89), change(48), water(23), not(21), people(20)
   📰 Titulares representativos:
      1. Solving California's Water Problems
      2. Life-Giving Deltas Starved by Dams
      3. The Deadly Cost Of North Dakota's Gas Boom

🏷️  C

### BONUS: Distribución de clusters (gráfico de barras)

In [52]:
# Usar nombres descriptivos para el gráfico de barras
cluster_dist = df['cluster'].value_counts().sort_index()
cluster_labels = [cluster_names.get(i, f'Cluster {i}') for i in cluster_dist.index]

fig_bar = px.bar(
    x=cluster_labels,
    y=cluster_dist.values,
    title="Distribución de Noticias por Cluster (Nombres Descriptivos)",
    labels={'x': 'Cluster', 'y': 'Número de Noticias'},
    color=cluster_dist.values,
    color_continuous_scale='Viridis'
)

fig_bar.update_layout(showlegend=False, xaxis_tickangle=-45)
fig_bar.show()


### OPCIONAL: Comparación con categorías originales

In [53]:
# Si el dataset tiene categoría, podemos validar
if 'category' in df.columns:
    print("\n" + "="*70)
    print("🔍 COMPARACIÓN CON CATEGORÍAS ORIGINALES")
    print("="*70)

    for cluster_id in sorted(df['cluster'].unique()):
        if cluster_id == -1:
            continue
        cluster_data = df[df['cluster'] == cluster_id]
        top_cats = cluster_data['category'].value_counts().head(3)
        cluster_name = cluster_names.get(cluster_id, f"Cluster {cluster_id}")

        print(f"\n🏷️  {cluster_name}:")
        for cat, count in top_cats.items():
            pct = count / len(cluster_data) * 100
            print(f"   - {cat}: {count} ({pct:.1f}%)")



🔍 COMPARACIÓN CON CATEGORÍAS ORIGINALES

🏷️  You & His (Game):
   - SPORTS: 173 (66.8%)
   - WELLNESS: 8 (3.1%)
   - ENTERTAINMENT: 8 (3.1%)

🏷️  Dog & Animal (His):
   - WEIRD NEWS: 28 (13.7%)
   - GREEN: 28 (13.7%)
   - ENVIRONMENT: 26 (12.7%)

🏷️  Climate & Change (Water):
   - POLITICS: 72 (30.3%)
   - GREEN: 58 (24.4%)
   - ENVIRONMENT: 27 (11.3%)

🏷️  Police & Not (Gun):
   - POLITICS: 208 (35.5%)
   - CRIME: 109 (18.6%)
   - COLLEGE: 35 (6.0%)

🏷️  You & Their (Kids):
   - PARENTING: 194 (45.5%)
   - PARENTS: 102 (23.9%)
   - WELLNESS: 18 (4.2%)

🏷️  Not & U.s. (Isis):
   - THE WORLDPOST: 88 (23.8%)
   - WORLDPOST: 73 (19.8%)
   - POLITICS: 70 (19.0%)

🏷️  Women & You (Her):
   - WOMEN: 31 (26.1%)
   - BUSINESS: 21 (17.6%)
   - IMPACT: 11 (9.2%)

🏷️  Gay & Marriage (Transgender):
   - QUEER VOICES: 136 (67.0%)
   - POLITICS: 25 (12.3%)
   - RELIGION: 6 (3.0%)

🏷️  You & Photos (Travel):
   - TRAVEL: 309 (46.3%)
   - HOME & LIVING: 108 (16.2%)
   - ARTS: 26 (3.9%)

🏷️  You & Foo

---
## 💾 EXPORTAR RESULTADOS (OPCIONAL)
---

In [54]:
# Descomentar para exportar a CSV
# df.to_csv('noticias_con_clusters.csv', index=False)
# print("✅ Resultados exportados a 'noticias_con_clusters.csv'")


---
## 📊 RESUMEN FINAL
---

In [55]:
print("\n" + "="*70)
print("📋 RESUMEN DEL CLUSTERING")
print("="*70)
print(f"Total de noticias procesadas: {len(df)}")
print(f"Clusters encontrados: {len([c for c in df['cluster'].unique() if c != -1])}")
print(f"Noticias clasificadas como ruido: {(df['cluster'] == -1).sum()} ({(df['cluster'] == -1).sum()/len(df)*100:.1f}%)")
print("\n✅ Pipeline completado exitosamente!")



📋 RESUMEN DEL CLUSTERING
Total de noticias procesadas: 9999
Clusters encontrados: 18
Noticias clasificadas como ruido: 3590 (35.9%)

✅ Pipeline completado exitosamente!


---
## 💾 GUARDAR MODELO PARA STREAMLIT
---

In [56]:
import pickle

print("\n" + "="*70)
print("💾 GUARDANDO MODELO PARA LA APLICACIÓN STREAMLIT")
print("="*70)

# Calcular centroides de cada cluster (usando embeddings originales 384D)
# IMPORTANTE: Usamos embeddings originales (384D) para compatibilidad con Streamlit
cluster_centroids = {}
for cluster_id in df['cluster'].unique():
    if cluster_id != -1:  # Ignorar ruido
        cluster_mask = df['cluster'] == cluster_id
        cluster_embeddings = embeddings[cluster_mask]  # ← Usar embeddings originales (384D)
        cluster_centroids[cluster_id] = cluster_embeddings.mean(axis=0)

print(f"\n✓ Centroides calculados para {len(cluster_centroids)} clusters (384D)")

# Guardar modelo completo
model_data = {
    'centroids': cluster_centroids,
    'cluster_names': cluster_names,
    'model_name': 'all-MiniLM-L6-v2',
    'n_clusters': len(cluster_centroids),
    'n_samples': len(df),
    'embedding_dimension': embeddings.shape[1],  # 384D
    'centroid_dimension': embeddings.shape[1]    # 384D (igual que embeddings)
}

# Guardar en archivo pickle
with open('model_data.pkl', 'wb') as f:
    pickle.dump(model_data, f)

print(f"✓ Modelo guardado en: model_data.pkl")

# Verificar el archivo guardado
import os
file_size = os.path.getsize('model_data.pkl') / 1024  # KB
print(f"✓ Tamaño del archivo: {file_size:.2f} KB")

# Mostrar información del modelo guardado
print(f"\n📊 Información del modelo guardado:")
print(f"   - Clusters: {model_data['n_clusters']}")
print(f"   - Noticias entrenadas: {model_data['n_samples']}")
print(f"   - Dimensión embeddings: {model_data['embedding_dimension']}D")
print(f"   - Dimensión centroides: {model_data['centroid_dimension']}D")
print(f"   - Modelo BERT: {model_data['model_name']}")

print("\n" + "="*70)
print("✅ MODELO LISTO PARA USAR EN STREAMLIT")
print("="*70)
print("\nAhora puedes ejecutar la aplicación Streamlit:")
print("   streamlit run app_streamlit.py")
print("\nLa app cargará automáticamente este modelo entrenado.")



💾 GUARDANDO MODELO PARA LA APLICACIÓN STREAMLIT

✓ Centroides calculados para 18 clusters (384D)
✓ Modelo guardado en: model_data.pkl
✓ Tamaño del archivo: 28.99 KB

📊 Información del modelo guardado:
   - Clusters: 18
   - Noticias entrenadas: 9999
   - Dimensión embeddings: 384D
   - Dimensión centroides: 384D
   - Modelo BERT: all-MiniLM-L6-v2

✅ MODELO LISTO PARA USAR EN STREAMLIT

Ahora puedes ejecutar la aplicación Streamlit:
   streamlit run app_streamlit.py

La app cargará automáticamente este modelo entrenado.


### Verificar que el modelo se puede cargar correctamente

In [57]:
# Test: cargar el modelo guardado
print("\n🧪 Verificando que el modelo se puede cargar...")

try:
    with open('model_data.pkl', 'rb') as f:
        loaded_data = pickle.load(f)

    print("✅ Modelo cargado exitosamente")
    print(f"   - Clusters cargados: {len(loaded_data['centroids'])}")
    print(f"   - Nombres de clusters disponibles: {len(loaded_data['cluster_names'])}")

    # Mostrar nombres de clusters
    print("\n🏷️ Clusters disponibles en el modelo:")
    for cluster_id, name in sorted(loaded_data['cluster_names'].items()):
        if cluster_id != -1:
            print(f"   {cluster_id}: {name}")

except Exception as e:
    print(f"❌ Error al cargar modelo: {e}")




🧪 Verificando que el modelo se puede cargar...
✅ Modelo cargado exitosamente
   - Clusters cargados: 18
   - Nombres de clusters disponibles: 19

🏷️ Clusters disponibles en el modelo:
   0: You & His (Game)
   1: Dog & Animal (His)
   2: Climate & Change (Water)
   3: Police & Not (Gun)
   4: You & Their (Kids)
   5: Not & U.s. (Isis)
   6: Women & You (Her)
   7: Gay & Marriage (Transgender)
   8: You & Photos (Travel)
   9: You & Food (It's)
   10: You & Health (Not)
   11: You & Our (Not)
   12: Trump & Donald (His)
   13: Tax & Health (You)
   14: You & Divorce (Marriage)
   15: Wedding & You (Her)
   16: Photos & You (Her)
   17: Trailer & Movie (You)
